In [ ]:
"""
Please save notebooks with important results to your own folder in JupyterHub.
See README for usage instructions:
https://git.zooxlabs.com/zooxco/driving/tree/master/mined_metric/jupyter/README.md
"""
from mined_metric.jupyter.utils.data_access_util import get_experiment_data, chum_summary_stats

EXPERIMENT_ID_TEST = "a211dbde-ae29-4c37-bf97-8f270432f9a0"
EXPERIMENT_ID_BASELINE = "c1ba2528-bb92-456c-a463-3419ef6c3791"

In [ ]:
# Retrieve all experiment data and metadata
exp_data_test = get_experiment_data(EXPERIMENT_ID_TEST)
if "exception" in exp_data_test:
    print("Invalid data is returned: %s" % exp_data_test["exception"])
exp_data_baseline = get_experiment_data(EXPERIMENT_ID_BASELINE)
if "exception" in exp_data_baseline:
    print("Invalid data is returned: %s" % exp_data_baseline["exception"])

In [ ]:
print("Copy and paste special (seperate columns by comma) the below into a google sheet for easy analysis:")
print("\n")
print("Original Chum,Argus Link,Mean Dist Error Test,Mean Dist Error Baseline,Mean Dist Error (Test - Baseline)")
for d_test in exp_data_test["meta"]:
    uri_test = d_test["chum_uri"]
    base_uri = uri_test.split('?')[0]
    # Find baseline data using the test uri
    d_baseline = []
    for search_d_baseline in exp_data_baseline["meta"]:
        if (search_d_baseline["chum_uri"].split('?')[0] == base_uri):
            d_baseline = search_d_baseline
    if (d_baseline == []):
        # No baseline found.
        print(str(uri)+ ",,,,,,,SIM_FAILURE")
        continue
        
    uri_baseline = d_baseline["chum_uri"]
        
    if "sim_failed" in d_test:
        # If the sim crashes or has a monitor we don't get data or a synthetic chum uri
        print(str(uri)+ ",,,,,,,SIM_FAILURE")
        continue
    if "sim_failed" in d_baseline:
        # If the sim crashes or has a monitor we don't get data or a synthetic chum uri
        print(str(uri)+ ",,,,,,,SIM_FAILURE")
        continue
        
    chum_uri_argus_link = "argus.zooxlabs.com/uri?primaryUri={}".format(uri_test.replace('&','%26')) \
                          + "&comparisonUri={}".format(uri_baseline.replace('&','%26')) \
                          + "&primaryNickname=Converted&comparisonNickname=Original"
    
    metric_test = d_test["agent_traj_metric"][0]
    metric_baseline = d_baseline["agent_traj_metric"][0]
    if ("mean_dist_error" in metric_test and "mean_dist_error" in metric_baseline):
        print(base_uri + "," + chum_uri_argus_link + "," + str(metric_test["mean_dist_error"]) + "," + str(metric_baseline["mean_dist_error"]) + "," + str(metric_test["mean_dist_error"] - metric_baseline["mean_dist_error"]))
    